# 03_Visualization_Feature_Investigation, Team 02

## 1—Import Libraries

In [21]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
from plotly.offline import iplot
import plotly.graph_objs as go
from scipy.stats import gaussian_kde
from scipy import stats
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectFromModel
pd.options.display.max_columns = None 

# 2—Read in Joined Dataset

In [22]:
df_joined = pd.read_csv('/data/p_dsi/teams2023/team2/ancient_artifacts_data/lithic_all_soil_joined_final.csv') 
df_joined.head(5)

Unnamed: 0     Id  Img Id      Da      Dp  FWidth  FLength  FThickness  \
0           0  104.0   10708  30.893  38.251  36.878   46.822      10.179   
1           1   19.0    5682  27.727  33.375  35.149   40.001       9.029   
2           2   14.0    4826  26.726  36.061  30.199   46.332       8.025   
3           3    1.0    2812  24.408  36.198  25.039   57.353       5.086   
4           4   83.0    9441  22.869  29.388  24.044   39.820       4.390   

   ELength  EThickness  EWidth    Volume     Area  Perimeter  CHull  Area  \
0   44.168      10.102  34.444  9202.973  749.562    120.170      802.914   
1   39.022       7.978  34.108  6646.859  603.785    104.849      636.820   
2   47.365       7.753  28.230  5879.233  560.995    113.290      642.874   
3   50.536       4.904  23.943  3824.409  467.900    113.719      500.291   
4   38.568       3.948  22.535  2200.862  410.744     92.327      436.309   

   CHull Perimeter  Sphericity  L/T Ratio  T/L Aspect Ratio  Compactness  \
0          108.399       0.808      4.600             0.217        0.660   
1           99.590       0.831      4.430             0.226        0.693   
2          100.583       0.741      5.774             0.173        0.577   
3          108.846       0.674     11.276             0.089        0.426   
4           89.254       0.778      9.070             0.110        0.574   

   Roundness  Ellipse Ratio  Circularity  Solidity  Concavity  Convexity  \
0      0.435          0.229        0.652     0.934      0.066      0.902   
1      0.480          0.204        0.690     0.948      0.052      0.950   
2      0.333          0.164        0.549     0.873      0.127      0.888   
3      0.181          0.097        0.455     0.935      0.065      0.957   
4      0.330          0.102        0.606     0.941      0.059      0.967   

   Extent  Transparency  Curvature  Surface Area  L/W Ratio  W/L Ratio  \
0   1.573         0.081        0.0      2998.247      1.270      0.788   
1   1.672         0.126        0.0      2415.141      1.138      0.879   
2   1.509         0.096        0.0      2243.981      1.534      0.652   
3   1.604         0.088        0.0      1871.602      2.291      0.437   
4   2.350         0.077        0.0      1642.977      1.656      0.604   

   W/T Ratio  T/W Ratio  CHull Surface Area   Sieve  Angularity  Ellipticity  \
0      3.623      0.276            3211.655  23.529      19.392        4.372   
1      3.893      0.257            2547.278  22.089      20.688        4.891   
2      3.763      0.266            2571.497  19.112      21.250        6.110   
3      4.923      0.203            2001.165  15.063      18.233       10.304   
4      5.477      0.183            1745.237  14.217      17.086        9.769   

   Fiber Length  Fiber Width  lithic  
0        49.768       22.823       1  
1        37.445        5.128       1  
2        52.384       17.379       1  
3        51.467       17.096       1  
4        36.426        3.135       1

In [23]:
# unsure why there is an extra first column, let's drop that
df_joined = df_joined.drop(df_joined.columns[0], axis=1)
df_joined.head(5)

Id  Img Id      Da      Dp  FWidth  FLength  FThickness  ELength  \
0  104.0   10708  30.893  38.251  36.878   46.822      10.179   44.168   
1   19.0    5682  27.727  33.375  35.149   40.001       9.029   39.022   
2   14.0    4826  26.726  36.061  30.199   46.332       8.025   47.365   
3    1.0    2812  24.408  36.198  25.039   57.353       5.086   50.536   
4   83.0    9441  22.869  29.388  24.044   39.820       4.390   38.568   

   EThickness  EWidth    Volume     Area  Perimeter  CHull  Area  \
0      10.102  34.444  9202.973  749.562    120.170      802.914   
1       7.978  34.108  6646.859  603.785    104.849      636.820   
2       7.753  28.230  5879.233  560.995    113.290      642.874   
3       4.904  23.943  3824.409  467.900    113.719      500.291   
4       3.948  22.535  2200.862  410.744     92.327      436.309   

   CHull Perimeter  Sphericity  L/T Ratio  T/L Aspect Ratio  Compactness  \
0          108.399       0.808      4.600             0.217        0.660   
1           99.590       0.831      4.430             0.226        0.693   
2          100.583       0.741      5.774             0.173        0.577   
3          108.846       0.674     11.276             0.089        0.426   
4           89.254       0.778      9.070             0.110        0.574   

   Roundness  Ellipse Ratio  Circularity  Solidity  Concavity  Convexity  \
0      0.435          0.229        0.652     0.934      0.066      0.902   
1      0.480          0.204        0.690     0.948      0.052      0.950   
2      0.333          0.164        0.549     0.873      0.127      0.888   
3      0.181          0.097        0.455     0.935      0.065      0.957   
4      0.330          0.102        0.606     0.941      0.059      0.967   

   Extent  Transparency  Curvature  Surface Area  L/W Ratio  W/L Ratio  \
0   1.573         0.081        0.0      2998.247      1.270      0.788   
1   1.672         0.126        0.0      2415.141      1.138      0.879   
2   1.509         0.096        0.0      2243.981      1.534      0.652   
3   1.604         0.088        0.0      1871.602      2.291      0.437   
4   2.350         0.077        0.0      1642.977      1.656      0.604   

   W/T Ratio  T/W Ratio  CHull Surface Area   Sieve  Angularity  Ellipticity  \
0      3.623      0.276            3211.655  23.529      19.392        4.372   
1      3.893      0.257            2547.278  22.089      20.688        4.891   
2      3.763      0.266            2571.497  19.112      21.250        6.110   
3      4.923      0.203            2001.165  15.063      18.233       10.304   
4      5.477      0.183            1745.237  14.217      17.086        9.769   

   Fiber Length  Fiber Width  lithic  
0        49.768       22.823       1  
1        37.445        5.128       1  
2        52.384       17.379       1  
3        51.467       17.096       1  
4        36.426        3.135       1

 # 3—Visualization & Feature Investigation

In [24]:
variables = list(df_joined.columns)
print(variables)

['Id', 'Img Id', 'Da', 'Dp', 'FWidth', 'FLength', 'FThickness', 'ELength', 'EThickness', 'EWidth', 'Volume', 'Area', 'Perimeter', 'CHull  Area', 'CHull Perimeter', 'Sphericity', 'L/T Ratio', 'T/L Aspect Ratio', 'Compactness', 'Roundness', 'Ellipse Ratio', 'Circularity', 'Solidity', 'Concavity', 'Convexity', 'Extent', 'Transparency', 'Curvature', 'Surface Area', 'L/W Ratio', 'W/L Ratio', 'W/T Ratio', 'T/W Ratio', 'CHull Surface Area', 'Sieve', 'Angularity', 'Ellipticity', 'Fiber Length', 'Fiber Width', 'lithic']


In [25]:
variable_measurements = variables[2:-1] 
# ignore Id, Img Id, and lithic since these aren't measurements of the particles themselves
print(variable_measurements)

['Da', 'Dp', 'FWidth', 'FLength', 'FThickness', 'ELength', 'EThickness', 'EWidth', 'Volume', 'Area', 'Perimeter', 'CHull  Area', 'CHull Perimeter', 'Sphericity', 'L/T Ratio', 'T/L Aspect Ratio', 'Compactness', 'Roundness', 'Ellipse Ratio', 'Circularity', 'Solidity', 'Concavity', 'Convexity', 'Extent', 'Transparency', 'Curvature', 'Surface Area', 'L/W Ratio', 'W/L Ratio', 'W/T Ratio', 'T/W Ratio', 'CHull Surface Area', 'Sieve', 'Angularity', 'Ellipticity', 'Fiber Length', 'Fiber Width']


In [26]:
# separate dataframe into one dataframe that just contains lithic particles and one that just contains soil particles
lithic_df = df_joined.loc[df_joined.loc[:, 'lithic'] == 1]
soil_df = df_joined.loc[df_joined.loc[:, 'lithic'] == 0]

In [27]:
lithic_df.shape[0]

4867

In [28]:
soil_df.shape[0]

# Thus, soil_df has 97,845 more rows than lithic_df (405,040 - 5299 = 399,741)

405040

In [43]:
# Let's make another soil df that has the same number of rows as the lithic dataframe to prepare 
# for plotting their distribution shapes

import random
soil_sample_ids = []
soil_df = soil_df.reset_index(drop = True)
soil_all_ids = list(soil_df.index.values)

for i in range (0, 4867):
    random_id = random.choice(soil_all_ids)
    soil_sample_ids.append(random_id)
    soil_all_ids.remove(random_id)

small_soil_df = pd.DataFrame(columns = soil_df.columns)
for i in range (0, 4867):
    soil_sample_row = soil_df.loc[soil_sample_ids[i]]
    small_soil_df.loc[len(small_soil_df)] = soil_sample_row
    
small_soil_df.head()

Id  Img Id     Da     Dp  FWidth  FLength  FThickness  ELength  \
0    8276.0  2309.0  0.256  0.264   0.267    0.297       0.200    0.299   
1   92527.0  4472.0  0.234  0.258   0.206    0.368       0.155    0.379   
2  136584.0  5678.0  0.258  0.289   0.252    0.406       0.156    0.405   
3  162221.0  6299.0  0.208  0.232   0.224    0.266       0.172    0.248   
4  154769.0  6125.0  0.247  0.266   0.257    0.448       0.182    0.437   

   EThickness  EWidth  Volume   Area  Perimeter  CHull  Area  CHull Perimeter  \
0       0.200   0.270   0.008  0.051      0.830        0.052            0.828   
1       0.156   0.209   0.006  0.043      0.809        0.044            0.805   
2       0.159   0.246   0.008  0.052      0.907        0.054            0.902   
3       0.168   0.231   0.005  0.034      0.729        0.036            0.700   
4       0.178   0.254   0.011  0.048      0.835        0.050            0.821   

   Sphericity  L/T Ratio  T/L Aspect Ratio  Compactness  Roundness  \
0       0.967      1.486             0.673        0.860      0.740   
1       0.907      2.383             0.420        0.635      0.403   
2       0.894      2.596             0.385        0.636      0.404   
3       0.895      1.547             0.647        0.783      0.613   
4       0.931      2.457             0.407        0.553      0.306   

   Ellipse Ratio  Circularity  Solidity  Concavity  Convexity  Extent  \
0          0.669        0.935     0.991      0.009      0.998   0.863   
1          0.412        0.823     0.968      0.032      0.994   0.754   
2          0.393        0.799     0.974      0.026      0.995   0.824   
3          0.679        0.802     0.950      0.050      0.960   0.745   
4          0.406        0.866     0.955      0.045      0.983   0.590   

   Transparency  Curvature  Surface Area  L/W Ratio  W/L Ratio  W/T Ratio  \
0         0.452      0.165         0.205      1.112      0.899      1.336   
1         0.473      0.000         0.172      1.787      0.560      1.333   
2         0.410      0.000         0.209      1.609      0.622      1.614   
3         0.487      1.188         0.136      1.183      0.845      1.308   
4         0.409      0.490         0.192      1.738      0.575      1.413   

   T/W Ratio  CHull Surface Area  Sieve  Angularity  Ellipticity  \
0      0.748               0.207  0.234      52.222        1.496   
1      0.750               0.177  0.180      60.000        2.429   
2      0.620               0.215  0.204      47.500        2.541   
3      0.765               0.143  0.198      70.000        1.474   
4      0.708               0.201  0.220      55.000        2.460   

   Fiber Length  Fiber Width  lithic  
0         0.000        0.000     0.0  
1         0.268        0.169     0.0  
2         0.340        0.145     0.0  
3         0.343        0.101     0.0  
4         0.393        0.180     0.0

In [44]:
# Graphs of the Density Plot for each Variable for Lithic vs Soil

def make_graphs(measurements):
    for measurement in measurements:
        lithic_col = lithic_df[measurement].values
        soil_col = small_soil_df[measurement].values
        
        kde1 = gaussian_kde(lithic_col)
        kde2 = gaussian_kde(soil_col)

        kde1.set_bandwidth(bw_method='silverman')
        kde2.set_bandwidth(bw_method='silverman')

        x = np.linspace(-3, 3, 1000)
        y1 = kde1(x)/max(kde1(x))
        y2 = kde2(x)/max(kde2(x))

        fig = go.Figure()

        fig.add_trace(go.Scatter(x=x, y=y1,mode='lines',
                                line=dict(width=1.5, color='blue'),
                                name='Lithic'))

        fig.add_trace(go.Scatter(x=x, y=y2,mode='lines',
                                line=dict(width=1.5, color='red'),
                                name='Soil'))

        fig.update_layout(xaxis_title=f"{measurement}",
                          yaxis_title="Density",
                          title = dict(text=f"Density Plot of {measurement} for Lithic and Soil Particles", 
                                       x=0.5, y=0.9, xanchor='center', yanchor='top'))
        fig.show()
        
make_graphs(variable_measurements)

# Based on the graphs, the following variables seem to have clearly distinct distributions for lithic vs soil:
# L/W Ratio, W/L Ratio, W/T Ratio, T/W Ratio, Fiber Length, Angularity

In [31]:
# displays the median for each variable for lithic vs soil as well as the difference in median 
df_medians = df_joined.groupby('lithic').median()
row_median_diff = df_medians.loc[1, :] - df_medians.loc[0, :]
row_median_diff=row_median_diff.to_frame() 
row_median_diff = row_median_diff.transpose()
df_medians = pd.concat([df_medians, row_median_diff], ignore_index=True)
df_medians

# row 1 is median of each variable for soil
# row 2 is median of each variable for lithic
# row 3 is median of each variable for lithic - median of each variable for soil 

Id   Img Id     Da     Dp  FWidth  FLength  FThickness  ELength  \
0  84503.0   4132.0  0.233  0.257   0.236    0.370       0.160     0.37   
1   2596.0  16606.0  0.200  0.259   0.144    0.353       0.135     0.33   
2 -81907.0  12474.0 -0.033  0.002  -0.092   -0.017      -0.025    -0.04   

   EThickness  EWidth  Volume   Area  Perimeter  CHull  Area  CHull Perimeter  \
0       0.157   0.230   0.008  0.043      0.806        0.045            0.790   
1       0.127   0.136   0.003  0.031      0.813        0.033            0.807   
2      -0.030  -0.094  -0.005 -0.012      0.007       -0.012            0.017   

   Sphericity  L/T Ratio  T/L Aspect Ratio  Compactness  Roundness  \
0       0.917      2.249             0.445        0.635      0.403   
1       0.814      2.577             0.388        0.598      0.358   
2      -0.103      0.328            -0.057       -0.037     -0.045   

   Ellipse Ratio  Circularity  Solidity  Concavity  Convexity  Extent  \
0          0.434        0.840     0.962      0.038      0.989   0.704   
1          0.393        0.663     0.969      0.031      0.997   0.710   
2         -0.041       -0.177     0.007     -0.007      0.008   0.006   

   Transparency  Curvature  Surface Area  L/W Ratio  W/L Ratio  W/T Ratio  \
0         0.452       0.23         0.171      1.538      0.650      1.417   
1         0.519       0.00         0.126      2.290      0.437      1.000   
2         0.067      -0.23        -0.045      0.752     -0.213     -0.417   

   T/W Ratio  CHull Surface Area  Sieve  Angularity  Ellipticity  \
0      0.706               0.180  0.201      58.571        2.303   
1      1.000               0.134  0.142      72.857        2.542   
2      0.294              -0.046 -0.059      14.286        0.239   

   Fiber Length  Fiber Width  
0         0.303        0.109  
1         0.278        0.086  
2        -0.025       -0.023

In [32]:
# displays the mean for each variable for lithic vs soil as well as the difference in means
df_means = df_joined.groupby('lithic').mean()
row_mean_diff = df_means.loc[1, :] - df_means.loc[0, :]
row_mean_diff=row_mean_diff.to_frame() 
row_mean_diff = row_mean_diff.transpose()
df_means = pd.concat([df_means, row_mean_diff], ignore_index=True)
df_means

# row 1 is mean of each variable for soil
# row 2 is mean of each variable for lithic
# row 3 is mean of each variable for lithic - mean of each variable for soil 

Id        Img Id        Da        Dp    FWidth   FLength  \
0  84512.327871   4267.637377  0.235721  0.264974  0.245976  0.400237   
1   2606.050339  16453.168276  0.435706  0.570239  0.376029  0.783191   
2 -81906.277532  12185.530900  0.199985  0.305265  0.130053  0.382954   

   FThickness   ELength  EThickness    EWidth     Volume      Area  Perimeter  \
0    0.166106  0.412247    0.162708  0.236790   0.009470  0.045112   0.832445   
1    0.233779  0.750398    0.220709  0.360588  18.075623  2.410687   1.791478   
2    0.067673  0.338151    0.058001  0.123798  18.066153  2.365575   0.959033   

   CHull  Area  CHull Perimeter  Sphericity  L/T Ratio  T/L Aspect Ratio  \
0     0.048595         0.806996    0.898132   2.433324          0.458013   
1     2.615329         1.744945    0.789125   3.000114          0.409072   
2     2.566735         0.937949   -0.109006   0.566790         -0.048941   

   Compactness  Roundness  Ellipse Ratio  Circularity  Solidity  Concavity  \
0     0.628491   0.412450       0.447582     0.811519  0.938984   0.061016   
1     0.595740   0.372119       0.414291     0.636881  0.941750   0.058250   
2    -0.032751  -0.040331      -0.033291    -0.174637  0.002766  -0.002766   

   Convexity    Extent  Transparency  Curvature  Surface Area  L/W Ratio  \
0   0.973635  0.693236      0.448029   0.348203      0.180456   1.616371   
1   0.990555  0.728856      0.496862   0.082719      9.642776   2.620799   
2   0.016920  0.035620      0.048832  -0.265484      9.462319   1.004428   

   W/L Ratio  W/T Ratio  T/W Ratio  CHull Surface Area     Sieve  Angularity  \
0   0.644866   1.495201   0.704437            0.194365  0.206041   60.441081   
1   0.450082   1.190738   0.924465           10.461324  0.304905   75.659567   
2  -0.194784  -0.304463   0.220028           10.266960  0.098865   15.218487   

   Ellipticity  Fiber Length  Fiber Width  
0     2.562985      0.305392     0.088829  
1     3.049431      0.641590     0.189826  
2     0.486446      0.336198     0.100997

In [33]:
# displays the std dev for each variable for lithic vs soil as well as the difference in std dev
df_std = df_joined.groupby('lithic').std()
row_std_diff = df_std.loc[1, :] - df_std.loc[0, :]
row_std_diff=row_std_diff.to_frame()
row_std_diff = row_std_diff.transpose()
df_std = pd.concat([df_std, row_std_diff], ignore_index=True)
df_std

# row 1 is std dev of each variable for soil
# row 2 is std dev of each variable for lithic
# row 3 is std dev of each variable for lithic - std dev of each variable for soil 

Id       Img Id        Da        Dp    FWidth   FLength  \
0  49657.781062  1317.340772  0.043319  0.059055  0.063511  0.140719   
1   1528.506851  1414.927416  1.697096  2.285343  1.756484  3.149506   
2 -48129.274212    97.586644  1.653776  2.226288  1.692974  3.008787   

   FThickness   ELength  EThickness    EWidth      Volume       Area  \
0    0.027670  0.162611    0.027804  0.058106    0.007076   0.017048   
1    0.688315  3.073592    0.649435  1.697813  246.362024  26.208650   
2    0.660645  2.910981    0.621631  1.639706  246.354949  26.191602   

   Perimeter  CHull  Area  CHull Perimeter  Sphericity  L/T Ratio  \
0   0.185520     0.020358         0.162640    0.069839   0.853917   
1   7.179621    28.395607         6.847754    0.118975   1.658684   
2   6.994102    28.375249         6.685114    0.049137   0.804767   

   T/L Aspect Ratio  Compactness  Roundness  Ellipse Ratio  Circularity  \
0          0.146616     0.132096   0.165517       0.160426     0.112995   
1          0.168495     0.131187   0.157149       0.179435     0.175121   
2          0.021879    -0.000910  -0.008368       0.019009     0.062126   

   Solidity  Concavity  Convexity    Extent  Transparency  Curvature  \
0  0.067957   0.067957   0.038402  0.126232      0.059868   0.398753   
1  0.080661   0.080661   0.019199  0.190891      0.093050   0.333667   
2  0.012704   0.012704  -0.019203  0.064659      0.033182  -0.065086   

   Surface Area  L/W Ratio  W/L Ratio  W/T Ratio  T/W Ratio  \
0      0.068180   0.351702   0.124408   0.377816   0.149433   
1    104.834599   1.255774   0.167193   0.587439   0.186165   
2    104.766419   0.904072   0.042785   0.209623   0.036732   

   CHull Surface Area     Sieve  Angularity  Ellipticity  Fiber Length  \
0            0.081429  0.039280    7.622810     1.017546      0.296410   
1          113.582422  1.193631   18.981306     1.884710      3.027353   
2          113.500993  1.154351   11.358496     0.867164      2.730942   

   Fiber Width  
0     0.078539  
1     0.921159  
2     0.842620

In [34]:
# T-Tests for each Variable 
t_test_df = pd.DataFrame(columns={'measurement': object, 't-statistic': float, 'p-value': float})

for measurement in variable_measurements:
    lithic_col = lithic_df[measurement].values
    soil_col = soil_df[measurement].values
    t, p = stats.ttest_ind(lithic_col, soil_col, equal_var=False)

    new_row = {'measurement': measurement, 't-statistic': t, 'p-value': p} 
    new_row_df = pd.DataFrame([new_row], columns=t_test_df.columns)
    t_test_df = pd.concat([t_test_df, new_row_df])

    
t_test_df['sig'] = np.where(t_test_df['p-value'] < 0.01, 'Sig', 'Not Sig')
t_test_df

measurement t-statistic   p-value      sig
0                  Da    8.220897       0.0      Sig
0                  Dp    9.318686       0.0      Sig
0              FWidth    5.165411       0.0      Sig
0             FLength    8.482609       0.0      Sig
0          FThickness    6.858879       0.0      Sig
0             ELength    7.675166       0.0      Sig
0          EThickness    6.230561       0.0      Sig
0              EWidth    5.086881       0.0      Sig
0              Volume    5.115906       0.0      Sig
0                Area    6.296842       0.0      Sig
0           Perimeter    9.318823       0.0      Sig
0         CHull  Area    6.306095       0.0      Sig
0     CHull Perimeter    9.555648       0.0      Sig
0          Sphericity  -63.786479       0.0      Sig
0           L/T Ratio   23.801187       0.0      Sig
0    T/L Aspect Ratio  -20.172165       0.0      Sig
0         Compactness  -17.311335       0.0      Sig
0           Roundness  -17.786178       0.0      Sig
0       Ellipse Ratio  -12.881739       0.0      Sig
0         Circularity  -69.397929       0.0      Sig
0            Solidity    2.382418  0.017237  Not Sig
0           Concavity    -2.38211  0.017251  Not Sig
0           Convexity    60.05523       0.0      Sig
0              Extent   12.983739       0.0      Sig
0        Transparency   36.521337       0.0      Sig
0           Curvature  -55.037795       0.0      Sig
0        Surface Area    6.296854       0.0      Sig
0           L/W Ratio   55.774176       0.0      Sig
0           W/L Ratio  -81.007984       0.0      Sig
0           W/T Ratio   -36.06831       0.0      Sig
0           T/W Ratio   82.136558       0.0      Sig
0  CHull Surface Area    6.306108       0.0      Sig
0               Sieve    5.778277       0.0      Sig
0          Angularity   55.879901       0.0      Sig
0         Ellipticity   17.974701       0.0      Sig
0        Fiber Length    7.747079       0.0      Sig
0         Fiber Width    7.648658       0.0      Sig

In [35]:
# Find the correlation between each variable and Lithic (the target we want to predict)

corr = df_joined.drop('lithic', axis=1).corrwith(df_joined['lithic'])
corr = corr.abs()
corr = corr.sort_values(ascending=False)
corr

# 'Img Id' is highly correlated with whether the particle is lithic/soil, haha #leakage 
# (don't use 'Img Id' or 'Id' as features in the ML Model)
# From this, L/W Ratio, W/L Ratio, Sphericity, Circularity, Angularity, T/W Ratio look pretty good 

Img Id                0.707470
L/W Ratio             0.278341
Angularity            0.205392
Id                    0.176894
W/L Ratio             0.166431
Sphericity            0.164898
Circularity           0.163789
T/W Ratio             0.156996
CHull Perimeter       0.131918
Perimeter             0.128186
Dp                    0.128184
Da                    0.113361
FLength               0.111242
ELength               0.098026
FThickness            0.091380
CHull Surface Area    0.089501
CHull  Area           0.089500
Surface Area          0.089371
Area                  0.089370
Transparency          0.087283
W/T Ratio             0.086239
Fiber Width           0.085718
EThickness            0.082421
Fiber Length          0.082059
Sieve                 0.078620
Volume                0.072710
Curvature             0.072057
L/T Ratio             0.070564
FWidth                0.069733
EWidth                0.069030
Ellipticity           0.050984
Convexity             0.047883
T/L Aspe

In [36]:
corr_matrix = df_joined.corr()

print(corr_matrix)

                          Id    Img Id        Da        Dp    FWidth  \
Id                  1.000000  0.564699 -0.019886 -0.015816 -0.001811   
Img Id              0.564699  1.000000  0.048139  0.062358  0.028172   
Da                 -0.019886  0.048139  1.000000  0.987756  0.964251   
Dp                 -0.015816  0.062358  0.987756  1.000000  0.940420   
FWidth             -0.001811  0.028172  0.964251  0.940420  1.000000   
FLength             0.002525  0.062816  0.951139  0.967964  0.916648   
FThickness         -0.028945  0.024952  0.895290  0.873634  0.832045   
ELength             0.008450  0.056649  0.930549  0.949749  0.899372   
EThickness         -0.029034  0.017878  0.887257  0.861943  0.823883   
EWidth             -0.005853  0.024823  0.964413  0.936933  0.996947   
Volume             -0.013200  0.023312  0.824388  0.799898  0.822584   
Area               -0.016133  0.031854  0.919316  0.905448  0.897846   
Perimeter          -0.015814  0.062361  0.987756  0.999999  0.94

In [37]:
# Find predictive variables using random forest 

df_joined_no_id = df_joined.drop(labels=['Img Id', 'Id'], axis=1)

X = df_joined_no_id.drop('lithic', axis = 1)
X_col_names = X.columns.tolist()
y = df_joined_no_id['lithic']

clf = RandomForestClassifier(random_state=0)
clf.fit(X, y)
 
selector = SelectFromModel(clf, threshold='median')

selector.fit(X, y)

X_important = selector.transform(X)

importances = clf.feature_importances_
feature_importance_df = pd.DataFrame(list(zip(X_col_names, importances)), columns=['feature_name', 'importance'])
feature_importance_df = feature_importance_df.sort_values(by='importance', ascending=False)
feature_importance_df

# Looks like Sieve, Surface Area, FThickness, FWidth are important 

feature_name  importance
32               Sieve    0.090960
9                 Area    0.085088
4           FThickness    0.084323
2               FWidth    0.082178
26        Surface Area    0.076684
0                   Da    0.075738
29           W/T Ratio    0.045925
6           EThickness    0.045523
27           L/W Ratio    0.043306
30           T/W Ratio    0.040525
28           W/L Ratio    0.038570
7               EWidth    0.028468
12     CHull Perimeter    0.025744
33          Angularity    0.024381
22           Convexity    0.019084
15    T/L Aspect Ratio    0.016843
14           L/T Ratio    0.016465
31  CHull Surface Area    0.015109
19         Circularity    0.014915
21           Concavity    0.013113
20            Solidity    0.012296
3              FLength    0.011918
11         CHull  Area    0.010230
13          Sphericity    0.009764
23              Extent    0.009352
10           Perimeter    0.008312
25           Curvature    0.007395
1                   Dp    0.007275
5              ELength    0.007263
36         Fiber Width    0.005419
24        Transparency    0.005078
35        Fiber Length    0.004463
8               Volume    0.004000
34         Ellipticity    0.003874
16         Compactness    0.003827
17           Roundness    0.003464
18       Ellipse Ratio    0.003126

In [38]:
df_joined_no_id = df_joined.drop(labels=['Img Id', 'Id'], axis=1)
df_circleness = df_joined_no_id[['Circularity', 'Sphericity', 'Roundness', 'Ellipse Ratio']]
cor_matrix_circleness = df_circleness.corr()
print(cor_matrix_circleness)

               Circularity  Sphericity  Roundness  Ellipse Ratio
Circularity       1.000000    0.993315   0.569512       0.483147
Sphericity        0.993315    1.000000   0.527652       0.430257
Roundness         0.569512    0.527652   1.000000       0.922115
Ellipse Ratio     0.483147    0.430257   0.922115       1.000000


In [39]:
df_roughness = df_joined_no_id[['Angularity', 'Concavity', 'Convexity', 'Solidity']]
cor_matrix_roughness = df_roughness.corr()
print(cor_matrix_roughness)

            Angularity  Concavity  Convexity  Solidity
Angularity    1.000000   0.172490  -0.209985 -0.172491
Concavity     0.172490   1.000000  -0.929484 -1.000000
Convexity    -0.209985  -0.929484   1.000000  0.929483
Solidity     -0.172491  -1.000000   0.929483  1.000000


In [40]:
df_asp_rat = df_joined_no_id[['L/W Ratio', 'W/L Ratio', 'T/W Ratio', 'W/T Ratio', 'L/T Ratio', 'T/L Aspect Ratio']]
cor_matrix_asp_rat = df_asp_rat.corr() 
print(cor_matrix_asp_rat) 

                  L/W Ratio  W/L Ratio  T/W Ratio  W/T Ratio  L/T Ratio  \
L/W Ratio          1.000000  -0.933698  -0.100743   0.075632   0.684082   
W/L Ratio         -0.933698   1.000000   0.161833  -0.120910  -0.691538   
T/W Ratio         -0.100743   0.161833   1.000000  -0.941037  -0.734010   
W/T Ratio          0.075632  -0.120910  -0.941037   1.000000   0.758691   
L/T Ratio          0.684082  -0.691538  -0.734010   0.758691   1.000000   
T/L Aspect Ratio  -0.657641   0.733305   0.776139  -0.707112  -0.908293   

                  T/L Aspect Ratio  
L/W Ratio                -0.657641  
W/L Ratio                 0.733305  
T/W Ratio                 0.776139  
W/T Ratio                -0.707112  
L/T Ratio                -0.908293  
T/L Aspect Ratio          1.000000  
